In [1]:
import altair as alt
import pandas as pd
import warnings

alt.data_transformers.disable_max_rows()

interval = alt.selection_interval(encodings=['x'])

warnings.simplefilter(action='ignore', category=FutureWarning)
df = pd.read_csv("/homes/adrian/mdr_mtb-master/results/summary/ABres/10_S4/DepthProfile_10_S4.csv", header = 0, sep = ',')
df["Gene"]=df["Gene"].str.split('_').str[0]

selector = alt.selection_single(empty="all", fields=["Gene"])
intervall_selector = alt.selection_interval(empty="all", encodings=['x'])

base = alt.Chart(df).transform_calculate(
    color = 'datum.Antibiotic !== "-" ? "red" : "lightgrey"'
)

base_selector = base.add_selection(selector)

barchart = base_selector.mark_bar().encode(
    x=alt.X("Gene:O", title = None,axis=alt.Axis(labelAngle=-45)),
    y="mean(Depth)",
    color = alt.condition(selector, alt.value("#1f77b4"), alt.value("lightgrey"))
).properties(title="Mean Depth per locus",width = 800, height = 200)

poschart = base_selector.mark_bar().encode(
    x="Position",
    y="Depth",
    color = alt.Color("color:N", scale = None),
).transform_filter(selector).add_selection(intervall_selector).properties(title="Locus specific depth",width = 350, height = 200)

zoom_chart = base.mark_bar().encode(
    x="Position",
    y="Depth",
    color = alt.Color("color:N", scale = None),
    tooltip=["Mutation:N", "Antibiotic:N"]
).transform_filter(intervall_selector).properties(title="Zoomed locus specific depth",width = 350, height = 200)

df2 = pd.read_csv("/homes/adrian/mdr_mtb-master/results/summary/ABres/10_S4/ABres_10_S4.csv", header = 0, sep = ',')
print(df2)
df2["Mut_gene"]=df2["Mut_gene"].str.split('_').str[0]
lsmut = []
lslocmut = []
for i in range(df2.shape[0]):
    lsmut.append(df2.loc[i]["Ref_Codon"]+str(df2.loc[i]["Codon_num"])+df2.loc[i]["Alt_Codon"])
    lslocmut.append(df2.loc[i]["Mut_gene"]+"_"+df2.loc[i]["Ref_Codon"]+str(df2.loc[i]["Codon_num"])+df2.loc[i]["Alt_Codon"])
df2["Mutation"]=lsmut
df2["LocMutation"]=lslocmut


base2 = alt.Chart(df2).encode(
    x=alt.X("Resistance",sort=["Resistance"],axis=alt.Axis(orient="top",labelAngle=35,labelFontSize=10,tickWidth=0,domain=False)),
).properties(width=350,height=100)

res = (base2.mark_circle(size=1800,color="red") +
       base2.mark_text(size=12).encode(text="Mut_gene") +
       base2.mark_text(dy=28,size=7).encode(text="Mutation"))

qual = alt.Chart(df2).mark_bar().encode(
    x=alt.X("LocMutation",sort=["Resistance"],axis=alt.Axis(orient="top",labelAngle=35,title="Mutation specifics",tickWidth=0)),
    y=alt.Y("Read_depth",axis=alt.Axis(title= "Read depth")),
    color = "Var_Qual",
    tooltip = ["Var_Qual","Read_depth"]
).properties(width=350,height=100)


(res | qual) & barchart & (poschart | zoom_chart)

  Mut_status                   Mut_gene  Genome_pos  Gene_pos  Codon_num  \
0    res_mut                       embB     4247429       916        306   
1    res_mut                       gyrA        7582       281         94   
2    res_mut                       rpoB      761155      1349        450   
3    res_mut                       rpsL      781687       128         43   
4    res_mut  fabG1_promoter_size_223bp     1673425       -15         -5   
5    res_mut    eis_promoter_size_119bp     2715342       -10         -3   
6    res_mut   katG_promoter_size_107bp     2155168       944        315   
7    res_mut   pncA_promoter_size_107bp     2289072       170         57   

   Codon_pos Ref_Codon Ref_aas Alt_Codon Alt_aas Var_type  AvLocus_Depth  \
0          1       ATG       M       GTG       V  ['snp']           3084   
1          2       GAC       D       GGC       G  ['snp']          13676   
2          2       TCG       S       TTG       L  ['snp']          30238   
3          

alt.VConcatChart(...)

In [2]:
import altair as alt
import pandas as pd
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)
alt.data_transformers.disable_max_rows()

abresprofile = "/homes/adrian/mdr_mtb-master/results/summary/ABres/10_S4/ABres_10_S4.csv"
depthprofile = "/homes/adrian/mdr_mtb-master/results/summary/ABres/10_S4/DepthProfile_10_S4.csv"

df = pd.read_csv(depthprofile, header = 0, sep = ',')
df["Gene"]=df["Gene"].str.split('_').str[0]

df2 = pd.read_csv(abresprofile, header = 0, sep = '\t')
df2["Mut_gene"]=df2["Mut_gene"].str.split('_').str[0]
lsmut = []
lslocmut = []
for i in range(df2.shape[0]):
    lsmut.append(df2.loc[i]["Ref_Codon"]+str(df2.loc[i]["Codon_num"])+df2.loc[i]["Alt_Codon"])
    lslocmut.append(df2.loc[i]["Mut_gene"]+"_"+df2.loc[i]["Ref_Codon"]+str(df2.loc[i]["Codon_num"])+df2.loc[i]["Alt_Codon"])
df2["Mutation"]=lsmut
df2["LocMutation"]=lslocmut

selector = alt.selection_single(empty="all", fields=["Gene"])
intervall_selector = alt.selection_interval(empty="all", encodings=['x'])

base = alt.Chart(df).transform_calculate(
    color = 'datum.Antibiotic !== "-" ? "red" : "lightgrey"',
)

base_selector = base.add_selection(selector)

barchart = base_selector.mark_bar().encode(
    x=alt.X("Gene:O", title = None,axis=alt.Axis(labelAngle=-45)),
    y=alt.Y("mean(Depth)",scale=alt.Scale(type="log")),
    color = alt.condition(selector, alt.value("#1f77b4"), alt.value("lightgrey")),
    tooltip = alt.Tooltip(["mean(Depth)"],format='.2f')
).properties(title="Mean Depth per locus",width = 800, height = 200)

poschart = base_selector.mark_bar().encode(
    x="Position",
    y="Depth",
    color = alt.Color("color:N", scale = None),
).transform_filter(selector).add_selection(intervall_selector).properties(title="Locus specific depth",width = 350, height = 200)

zoom_chart = base.mark_bar().encode(
    x="Position",
    y="Depth",
    color = alt.Color("color:N", scale = None),
    tooltip=["Mutation:N", "Antibiotic:N"]
).transform_filter(intervall_selector).properties(title="Zoomed locus specific depth",width = 350, height = 200)

base2 = alt.Chart(df2).encode(
    x=alt.X("Resistance",sort=["Resistance"],axis=alt.Axis(orient="top",labelAngle=35,labelFontSize=10,tickWidth=0,domain=False)),
).properties(width=350,height=100)

res = (base2.mark_circle(size=1800,color="red") +
       base2.mark_text(size=12).encode(text="Mut_gene") +
       base2.mark_text(dy=28,size=7).encode(text="Mutation"))

qual = alt.Chart(df2).mark_bar(color="#1f77b4").encode(
    x=alt.X("LocMutation",sort=["Resistance"],axis=alt.Axis(orient="top",labelAngle=35,title="Mutation specifics",tickWidth=0)),
    y=alt.Y("Read_depth",scale=alt.Scale(type="log"),axis=alt.Axis(title= "Read depth")),
    tooltip = ["Var_Qual","Read_depth"]
).properties(width=350,height=100)


plot = (res | qual) & barchart & (poschart | zoom_chart)
plot

KeyError: 'Mut_gene'

In [3]:
import altair as alt
import pandas as pd
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)
alt.data_transformers.disable_max_rows()

abresprofile = "/homes/adrian/mdr_mtb-master/results/summary/ABres/3_S3/ABres_3_S3.csv"
depthprofile = "/homes/adrian/mdr_mtb-master/results/summary/ABres/3_S3/DepthProfile_3_S3.csv"

df = pd.read_csv(depthprofile, header = 0, sep = ',')
df["Gene"]=df["Gene"].str.split('_').str[0]

df2 = pd.read_csv(abresprofile, header = 0, sep = '\t')
df2["Mut_gene"]=df2["Mut_gene"].str.split('_').str[0]
lsmut = []
lslocmut = []
for i in range(df2.shape[0]):
    lsmut.append(df2.loc[i]["Ref_Codon"]+str(df2.loc[i]["Codon_num"])+df2.loc[i]["Alt_Codon"])
    lslocmut.append(df2.loc[i]["Mut_gene"]+"_"+df2.loc[i]["Ref_Codon"]+str(df2.loc[i]["Codon_num"])+df2.loc[i]["Alt_Codon"])
df2["Mutation"]=lsmut
df2["LocMutation"]=lslocmut

selector = alt.selection_single(empty="all", fields=["Gene"])
intervall_selector = alt.selection_interval(empty="all", encodings=['x'])

base = alt.Chart(df).transform_calculate(
    color = 'datum.Antibiotic !== "-" ? "red" : "lightgrey"',
)

base_selector = base.add_selection(selector)

barchart = base_selector.mark_bar().encode(
    x=alt.X("Gene:O", title = None,axis=alt.Axis(labelAngle=-45)),
    y=alt.Y("mean(Depth)",scale=alt.Scale(type="log")),
    color = alt.condition(selector, alt.value("#1f77b4"), alt.value("lightgrey")),
    tooltip = alt.Tooltip(["mean(Depth)"],format='.2f')
).properties(title="Mean Depth per locus",width = 780, height = 200)

poschart = base_selector.mark_bar().encode(
    x="Position",
    y="Depth",
    color = alt.Color("color:N", scale = None),
).transform_filter(selector).add_selection(intervall_selector).properties(title="Locus specific depth",width = 350, height = 200)

zoom_chart = base.mark_bar().encode(
    x="Position",
    y="Depth",
    color = alt.Color("color:N", scale = None),
    tooltip=["Mutation:N", "Antibiotic:N", "Depth"]
).transform_filter(intervall_selector).properties(title="Zoomed locus specific depth",width = 350, height = 200)

base2 = alt.Chart(df2).transform_calculate(
    color = 'datum.Resistance !== "-" ? "red" : "blue"',
).encode(
    x=alt.X("Resistance",sort=["Resistance"],axis=alt.Axis(orient="top",labelAngle=35,labelFontSize=10,tickWidth=0,domain=False)),
).properties(width=360,height=100)

res = (base2.mark_circle(size=1800).encode(color = alt.Color("color:N", scale = None)) +
       base2.mark_text(size=12).encode(text="Mut_gene") +
       base2.mark_text(dy=28,size=7).encode(text="Mutation"))

qual = alt.Chart(df2).mark_bar(color="#1f77b4").encode(
    x=alt.X("LocMutation",sort=["Resistance"],axis=alt.Axis(orient="top",labelAngle=35,title="Mutation specifics",tickWidth=0)),
    y=alt.Y("Read_depth",scale=alt.Scale(type="log"),axis=alt.Axis(title= "Read depth")),
    tooltip = ["Var_Qual","Read_depth"]
).properties(width=360,height=100)


plot = alt.vconcat((res | qual), barchart, (poschart | zoom_chart),title=alt.TitleParams(
    text="Resistance plot",anchor="middle",fontWeight="bold",fontSize=20))
plot

KeyError: 'Mut_gene'

In [51]:
import pandas as pd

depthsum1 = "/homes/adrian/mdr_mtb-master/results/10/samtools_depth/1_S1/1_S1_coverage_summary.txt"
depthsum2 = "/homes/adrian/mdr_mtb-master/results/60/samtools_depth/1_S1/1_S1_coverage_summary.txt"

df = pd.read_csv(depthsum1, header= 0, sep = '\t')
df["#rname"]=df["#rname"].str.split('_').str[0]
df["startpos"]=df["endpos"]-df["startpos"]+1
df=df.drop(["endpos"],axis=1)
df=df.rename(columns={"#rname":"locus","startpos":"numpos"})
df.insert(1, 'read_reduction', 10)

df2 = pd.read_csv(depthsum1, header= 0, sep = '\t')
df2["#rname"]=df2["#rname"].str.split('_').str[0]
df2["startpos"]=df2["endpos"]-df2["startpos"]+1
df2=df2.drop(["endpos"],axis=1)
df2=df2.rename(columns={"#rname":"locus","startpos":"numpos"})
df2.insert(1, 'read_reduction', 60)
frames = [df,df2]

df3 = pd.concat(frames).sort_values(['locus','read_reduction'])
df3

locus  read_reduction  numpos  numreads  covbases  coverage   meandepth  \
20    ahpC              10     768     23386       587   76.4323   4231.4800   
20    ahpC              60     768     23386       587   76.4323   4231.4800   
12     alr              10    1227         0         0    0.0000      0.0000   
12     alr              60    1227         0         0    0.0000      0.0000   
14    drrA              10     996         0         0    0.0000      0.0000   
14    drrA              60     996         0         0    0.0000      0.0000   
22     eis              10    1328    243532       299   22.5151  22288.7000   
22     eis              60    1328    243532       299   22.5151  22288.7000   
21    embA              10    3400         0         0    0.0000      0.0000   
21    embA              60    3400         0         0    0.0000      0.0000   
0     embB              10    3297      2991       724   21.9594    128.9390   
0     embB              60    3297      2991       724   21.9594    128.9390   
16    embC              10    3285         0         0    0.0000      0.0000   
16    embC              60    3285         0         0    0.0000      0.0000   
17    embR              10    1167         0         0    0.0000      0.0000   
17    embR              60    1167         0         0    0.0000      0.0000   
23    ethA              10    1544      9228      1501   97.2150    499.0240   
23    ethA              60    1544      9228      1501   97.2150    499.0240   
19   fabG1              10     967     32894       469   48.5005   4845.9900   
19   fabG1              60     967     32894       469   48.5005   4845.9900   
15    folC              10    1464         0         0    0.0000      0.0000   
15    folC              60    1464         0         0    0.0000      0.0000   
1     gidB              10     675      1241       675  100.0000    247.2900   
1     gidB              60     675      1241       675  100.0000    247.2900   
2     gyrA              10    2517     26902       419   16.6468   1520.1900   
2     gyrA              60    2517     26902       419   16.6468   1520.1900   
3     gyrB              10    2028     12297       688   33.9250    869.6810   
3     gyrB              60    2028     12297       688   33.9250    869.6810   
4     inhA              10     810     21569       646   79.7531   3829.4500   
4     inhA              60     810     21569       646   79.7531   3829.4500   
24    katG              10    2330      2612       750   32.1888    159.8850   
24    katG              60    2330      2612       750   32.1888    159.8850   
13    panD              10     420         0         0    0.0000      0.0000   
13    panD              60     420         0         0    0.0000      0.0000   
25    pncA              10     668     10677       637   95.3593   2296.6400   
25    pncA              60     668     10677       637   95.3593   2296.6400   
18    ribD              10     777         0         0    0.0000      0.0000   
18    ribD              60     777         0         0    0.0000      0.0000   
5     rplC              10     654     27072       373   57.0336   5728.5700   
5     rplC              60     654     27072       373   57.0336   5728.5700   
6     rpoB              10    3519    136474      1008   28.6445   5489.7600   
6     rpoB              60    3519    136474      1008   28.6445   5489.7600   
7     rpsL              10     375     35036       375  100.0000  12570.9000   
7     rpsL              60     375     35036       375  100.0000  12570.9000   
8      rrl              10    3138      1678       882   28.1071     76.1409   
8      rrl              60    3138      1678       882   28.1071     76.1409   
9      rrs              10    1537      1222      1537  100.0000    114.4900   
9      rrs              60    1537      1222      1537  100.0000    114.4900   
10  rv0678              10     498      6817       498  100.0000   1849.8800   
10  r

In [4]:
import altair as alt
import pandas as pd
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)
alt.data_transformers.disable_max_rows()

abresprofile1 = "/homes/adrian/mdr_mtb-master/results1.run_0-90/10/ABres/3_S3/ABres_3_S3.csv"
depthprofile1 = "/homes/adrian/mdr_mtb-master/results1.run_0-90/10/ABres/3_S3/DepthProfile_3_S3.csv"
abresprofile2 = "/homes/adrian/mdr_mtb-master/results1.run_0-90/60/ABres/3_S3/ABres_3_S3.csv"
depthprofile2 = "/homes/adrian/mdr_mtb-master/results1.run_0-90/60/ABres/3_S3/DepthProfile_3_S3.csv"

sminput1=[abresprofile1,abresprofile2]
sminput2=[depthprofile1,depthprofile2]

param = ["10","60"]

i=0
lis = []
for depthprofile,abresprofile,par in zip(sminput2,sminput1,param):
    df = pd.read_csv(depthprofile, header = 0, sep = ',')
    df["Gene"]=df["Gene"].str.split('_').str[0]

    df2 = pd.read_csv(abresprofile, header = 0, sep = '\t')
    df2["Mut_gene"]=df2["Mut_gene"].str.split('_').str[0]
    lsmut = []
    lslocmut = []
    for i in range(df2.shape[0]):
        lsmut.append(df2.loc[i]["Ref_Codon"]+str(df2.loc[i]["Codon_num"])+df2.loc[i]["Alt_Codon"])
        lslocmut.append(df2.loc[i]["Mut_gene"]+"_"+df2.loc[i]["Ref_Codon"]+str(df2.loc[i]["Codon_num"])+df2.loc[i]["Alt_Codon"])
    df2["Mutation"]=lsmut
    df2["LocMutation"]=lslocmut
    barchart = alt.Chart(df).mark_bar(color = "#1f77b4").encode(
        x=alt.X("Gene:O", title = None,axis=alt.Axis(labelAngle=-45)),
        y=alt.Y("mean(Depth)",scale=alt.Scale(type="log")),
        tooltip = alt.Tooltip(["mean(Depth)"],format='.2f')
    ).properties(title="Mean Depth per locus",width = 780, height = 200)

    base2 = alt.Chart(df2).transform_calculate(
        color = 'datum.Resistance !== "-" ? "red" : "blue"',
    ).encode(
        x=alt.X("Resistance",sort=["Resistance"],axis=alt.Axis(orient="top",labelAngle=35,labelFontSize=10,tickWidth=0,domain=False)),
    ).properties(width=360,height=100)

    res = (base2.mark_circle(size=1800).encode(color = alt.Color("color:N", scale = None)) +
           base2.mark_text(size=12).encode(text="Mut_gene") +
           base2.mark_text(dy=28,size=7).encode(text="Mutation"))

    qual = alt.Chart(df2).mark_bar(color="#1f77b4").encode(
        x=alt.X("LocMutation",sort=["Resistance"],axis=alt.Axis(orient="top",labelAngle=35,title="Mutation specifics",tickWidth=0)),
        y=alt.Y("Read_depth",scale=alt.Scale(type="log"),axis=alt.Axis(title= "Read depth")),
        tooltip = ["Var_Qual","Read_depth"]
    ).properties(width=360,height=100)
    lis.append(alt.vconcat((res | qual), barchart,title=alt.TitleParams(
        text="Resistance plot -"+par+"%",anchor="middle",fontWeight="bold",fontSize=20)))
a=alt.hconcat(*lis)
a.save(snakemake.output[0])

KeyError: 'Mut_gene'

In [11]:
import pandas as pd
import altair as alt

abresprofile1 = "/homes/adrian/mdr_mtb-master/results/summary/ABres/10_S4/ABres_10_S4.csv"
depthprofile1 = "/homes/adrian/mdr_mtb-master/results/summary/ABres/10_S4/DepthProfile_10_S4.csv"
abresprofile2 = "/homes/adrian/mdr_mtb-master/results/summary/ABres/1_S1/ABres_1_S1.csv"
depthprofile2 = "/homes/adrian/mdr_mtb-master/results/summary/ABres/1_S1/DepthProfile_1_S1.csv"

ab_df = pd.read_csv(abresprofile1, header = 0, sep = ',')
dp_df = pd.read_csv(depthprofile1, header = 0, sep = ',')
ab_df2 = pd.read_csv(abresprofile2, header = 0, sep = ',')
dp_df2 = pd.read_csv(depthprofile2, header = 0, sep = ',')

dp_df["Gene"]=dp_df["Gene"].str.split('_').str[0]
ab_df["Mut_gene"]=ab_df["Mut_gene"].str.split('_').str[0]
lsmut = []
lslocmut = []
for i in range(ab_df.shape[0]):
    lsmut.append(ab_df.loc[i]["Ref_Codon"]+str(ab_df.loc[i]["Codon_num"])+ab_df.loc[i]["Alt_Codon"])
    lslocmut.append(ab_df.loc[i]["Mut_gene"]+"_"+ab_df.loc[i]["Ref_Codon"]+str(ab_df.loc[i]["Codon_num"])+ab_df.loc[i]["Alt_Codon"])
ab_df["Mutation"]=lsmut
ab_df["LocMutation"]=lslocmut

selector = alt.selection_single(empty="all", fields=["Gene"])
intervall_selector = alt.selection_interval(empty="all", encodings=['x'])

base = alt.Chart(dp_df).transform_calculate(
    color = 'datum.Antibiotic !== "-" ? "red" : "lightgrey"',
)

base_selector = base.add_selection(selector)

barchart = base_selector.mark_bar().encode(
    x=alt.X("Gene:O", title = None,axis=alt.Axis(labelAngle=-45)),
    y=alt.Y("mean(Depth):Q",scale=alt.Scale(type="log")),
    tooltip = alt.Tooltip(["mean(Depth)"],format='.2f'),
    color=alt.condition(selector, alt.value("#1f77b4"), alt.value("lightgrey")),
).properties(title="Mean Depth per locus",width = 795, height = 200)

poschart = base_selector.mark_bar().encode(
    x="Position",
    y="Depth",
    color = alt.Color("color:N", scale = None),
).transform_filter(selector).add_selection(intervall_selector).properties(title="Locus specific depth",width = 355, height = 200)

zoom_chart = base.mark_bar().encode(
    x="Position",
    y="Depth",
    color = alt.Color("color:N", scale = None),
    tooltip=["Mutation:N", "Antibiotic:N", "Depth"]
).transform_filter(intervall_selector).properties(title="Zoomed locus specific depth",width = 355, height = 200)


base2 = alt.Chart(ab_df).transform_calculate(
    color = 'datum.Resistance !== "-" ? "red" : "blue"',
).encode(
    x=alt.X("Resistance",sort=["Resistance"],axis=alt.Axis(orient="top",labelAngle=35,labelFontSize=10,tickWidth=0,domain=False)),
).properties(width=360,height=100)

res = (base2.mark_circle(size=1800).encode(color = alt.Color("color:N", scale = None)) +
       base2.mark_text(size=12).encode(text="Mut_gene") +
       base2.mark_text(dy=28,size=7).encode(text="Mutation").properties(width=350,height=100))

qual = alt.Chart(ab_df).mark_bar(color="#1f77b4").encode(
    x=alt.X("LocMutation",sort=["Resistance"],axis=alt.Axis(orient="top",labelAngle=35,title="Mutation specifics",tickWidth=0)),
    y=alt.Y("Read_depth",scale=alt.Scale(type="log"),axis=alt.Axis(title= "Read depth")),
    tooltip = ["Var_Qual","Read_depth"]
).properties(width=350,height=100)

plot = alt.vconcat((res | qual), barchart, (poschart | zoom_chart))
plot

alt.VConcatChart(...)

In [75]:
import pandas as pd
import altair as alt
import warnings
from altair.expr import datum, if_

alt.data_transformers.disable_max_rows()
warnings.simplefilter(action='ignore', category=FutureWarning)
warnings.simplefilter(action='ignore', category=UserWarning)

abresprofile = "/homes/adrian/mdr_mtb-master/results/summary/ABres/10_S4/ABres_10_S4.csv"
depthprofile = "/homes/adrian/mdr_mtb-master/results/summary/ABres/10_S4/DepthProfile_10_S4.csv"

ab_df = pd.read_csv(abresprofile, header = 0, sep = ',')
dp_df = pd.read_csv(depthprofile, header = 0, sep = ',')

dp_df["Gene"]=dp_df["Gene"].str.split('_').str[0]
ab_df["Mut_gene"]=ab_df["Mut_gene"].str.split('_').str[0]
lsmut = []
lslocmut = []
for i in range(ab_df.shape[0]):
    lsmut.append(ab_df.loc[i]["Ref_Codon"]+str(ab_df.loc[i]["Codon_num"])+ab_df.loc[i]["Alt_Codon"])
    lslocmut.append(ab_df.loc[i]["Mut_gene"]+"_"+ab_df.loc[i]["Ref_Codon"]+str(ab_df.loc[i]["Codon_num"])+ab_df.loc[i]["Alt_Codon"])
ab_df["Mutation"]=lsmut
ab_df["LocMutation"]=lslocmut
ab_df = ab_df[ab_df["Mut_status"] == "res_mut"]

selector = alt.selection_single(empty="all", fields=["Gene"])
intervall_selector = alt.selection_interval(empty="all", encodings=['x'])

base = alt.Chart(dp_df).transform_calculate(
    color = 'datum.Antibiotic !== "-" ? "red" : "lightgrey"',
)

base_selector = base.add_selection(selector)

barchart = base_selector.mark_bar().encode(
    x=alt.X("Gene:O", title = None,axis=alt.Axis(labelAngle=-45)),
    y=alt.Y("mean(Depth):Q",scale=alt.Scale(type="log")),
    tooltip = alt.Tooltip(["mean(Depth)"],format='.2f'),
    color=alt.condition(selector, alt.value("#1f77b4"), alt.value("lightgrey")),
).properties(title="Mean Depth per locus",width = 798, height = 200)

poschart = base_selector.mark_bar().encode(
    x="Position",
    y="Depth",
    color = alt.Color("color:N", scale = None),
).transform_filter(selector).add_selection(intervall_selector).properties(title="Locus specific depth",width = 356, height = 200)

zoom_chart = base.mark_bar().encode(
    x="Position",
    y="Depth",
    color = alt.Color("color:N", scale = None),
    tooltip=["Mutation:N", "Antibiotic:N", "Depth"]
).transform_filter(intervall_selector).properties(title="Zoomed locus specific depth",width = 356, height = 200)


base2 = alt.Chart(ab_df).transform_calculate(
    color = 'datum.Var_Qual >= 1 ? "red" : "orange"',
).encode(
    x=alt.X("Resistance",sort=["Resistance"],axis=alt.Axis(orient="top",labelAngle=35,labelFontSize=10,tickWidth=0,domain=False)),
    tooltip=["AvLocus_Depth", "Read_depth", "Alt_num", "Var_Qual"]
).properties(width=355,height=100)

res = (base2.mark_circle(size=1800).encode(color = alt.Color("color:N", scale = None)) +
       base2.mark_text(size=12).encode(text="Mut_gene") +
       base2.mark_text(dy=28,size=7).encode(text="Mutation"))

qual = alt.Chart(ab_df).mark_bar(color="#1f77b4").encode(
    x=alt.X("LocMutation",sort=["Resistance"],axis=alt.Axis(orient="top",labelAngle=35,title="Mutation specifics",tickWidth=0)),
    y=alt.Y("Read_depth",scale=alt.Scale(type="log"),axis=alt.Axis(title= "Read depth")),
    tooltip = ["Var_Qual","Read_depth"]
).properties(width=355,height=100)

plot = alt.vconcat((res | qual), barchart, (poschart | zoom_chart))
plot

alt.VConcatChart(...)

In [98]:
import pandas as pd
import altair as alt
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)


df = pd.read_csv("/homes/adrian/mdr_mtb-master/results1.run_0-90/summary_edited.csv", header = 0, sep = '\t')
df['Sample'] = df['Sample'].str.split('_').str[0]
dfsort = df.loc[df["reduction"] == 0]

df2 = pd.read_csv("/homes/adrian/mdr_mtb-master/results1.run_0-90/coverage.csv", header = 0, sep = '\t')
df2['Sample'] = df2['Sample'].str.split('_').str[0]
#df2 = df2.loc[df2["reduction"] == 0]
common_cols=list(set.intersection(set(df['Sample']), set(df2['Sample'])))
df2 = df2[df2['Sample'].isin(common_cols)]

one = alt.Chart(df).mark_rect(stroke="white",strokeWidth=0.1).encode(
    y=alt.Y("Sample:O",sort=dfsort["Sample"].to_list(),title=None),
    x=alt.X("reduction:O",title="Reduction [%]"),
    color=alt.Color("res_mutation",title="Resistance mutations",legend=alt.Legend(orient="bottom"))
).properties(title="Resistance causing mutations",width=200)

two = alt.Chart(df).mark_rect(stroke="white",strokeWidth=0.1).encode(
    y=alt.Y("Sample:O",sort=dfsort["Sample"].to_list(),title=None),
    x=alt.X("reduction:O",title="Reduction [%]"),
    color=alt.Color("total_mutation",title="Total mutations",legend=alt.Legend(orient="bottom"))
).properties(title="Total mutations",width=200)

three = alt.Chart(df2).mark_bar(stroke="white",strokeWidth=0.1).encode(
    y=alt.Y("Sample:O",sort=df2["Sample"].to_list()),
    x=alt.X("mean_coverage:Q",scale=alt.Scale(type="sqrt",align=0),stack=None,title="Mean coverage"),
    color=alt.Color("stabw_coverage",title="Standard deviation",legend=alt.Legend(orient="bottom"))
).properties(title="Mean locus coverage 10-100%",width=200)

plot = alt.hconcat(three,one,two).resolve_scale(color='independent').properties(
    title=alt.TitleParams(text="Read reduction summary",anchor="middle",fontWeight="bold",fontSize=16))
plot

alt.HConcatChart(...)

In [4]:
import pandas as pd
import altair as alt
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)


dfres = pd.read_csv("/homes/adrian/mdr_mtb-master/results1.run_0-90/resistances_edited.csv", header = 0, sep = '\t')
dfres['Sample'] = dfres['Sample'].str.split('_').str[0]
dfres["resistance"] = dfres["resistance"].replace({
    'RIFAMPICIN' : 'RIF','ISONIAZID' : 'INH','KANAMYCIN' : 'KAN','PYRAZINAMIDE' : 'PZA','ETHAMBUTOL' : 'EMB',\
    'ETHIONAMIDE' : 'ETH','STREPTOMYCIN' : 'SM','FLUOROQUINOLONE' : 'FQ',})
sorting = ["RIF","INH","PZA","EMB","SM","FQ","KAN","AMI","CAP","ETH","LIN","BDQ","CFZ"]


plot = alt.Chart(dfres).mark_rect(stroke="black",strokeWidth=0.1).encode(
    y=alt.Y("Sample:O",sort=dfres["Sample"].to_list()),
    x=alt.X("resistance:O",axis=alt.Axis(orient="top",title="Resistotype",tickWidth=0),sort=sorting),
    color=alt.condition("datum.quality >= 1", alt.ColorValue("#FF3000"), alt.ColorValue("darkorange")),
    #legend=alt.Legend(title="Banana")
    opacity=alt.Opacity('quality',bin=alt.Bin(extent=[0,5]),legend=alt.Legend(title=["Variant quality", "MYCRes"]))
).properties(title="Resistances MYCRes")

plot1 = alt.Chart(dfres).mark_rect(stroke="black",strokeWidth=0.1).encode(
    y=alt.Y("Sample:O",sort=dfres["Sample"].to_list()),
    x=alt.X("resistance:O",axis=alt.Axis(orient="top",title="Resistotype",tickWidth=0),sort=sorting),
    color=alt.condition("datum.quality >= 1", alt.ColorValue("#FF3000"), alt.ColorValue("darkorange")),
    #legend=alt.Legend(title="Banana")
    #opacity=alt.Opacity('quality',bin=alt.Bin(extent=[0,5]),legend=alt.Legend(title="Variant quality"))
).properties(title="Resistances MYCRes")
plot | plot1

alt.HConcatChart(...)

In [3]:
import pandas as pd
import altair as alt
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)


dfres = pd.read_csv("/homes/adrian/mdr_mtb-master/resultsSRR_0/resistances.csv", header = 0, sep = '\t')
dfres['Sample'] = dfres['Sample'].str.replace('SRR','')
dfres["resistance"] = dfres["resistance"].replace({
    'RIFAMPICIN' : 'RIF','ISONIAZID' : 'INH','KANAMYCIN' : 'KAN','PYRAZINAMIDE' : 'PZA','ETHAMBUTOL' : 'EMB',\
    'ETHIONAMIDE' : 'ETH','STREPTOMYCIN' : 'SM','FLUOROQUINOLONE' : 'FQ', 'AMIKACIN' : 'AMI', \
    'CAPREOMYCIN' : 'CAP', 'LINEZOLID' : 'LIN'
})
sorting = ["RIF","INH","PZA","EMB","SM","FQ","KAN","AMI","CAP","ETH","LIN","BDQ","CFZ"]


plot = alt.Chart(dfres).mark_rect(stroke="black",strokeWidth=0.1).encode(
    y=alt.Y("Sample:O",sort=dfres["Sample"].to_list()),
    x=alt.X("resistance:O",axis=alt.Axis(orient="top",title="Resistotype",tickWidth=0),sort=sorting),
    color=alt.condition("datum.quality >= 1", alt.ColorValue("#FF3000"), alt.ColorValue("darkorange"))
    
).properties(title="Resistances third sample set",width=200)
plot

alt.Chart(...)

In [43]:
import pandas as pd
import altair as alt
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)


dfres = pd.read_csv("/homes/adrian/mdr_mtb-master/results3.run_0-90/resistances.csv", header = 0, sep = '\t')
dfres['Sample'] = dfres['Sample'].str.split('_S').str[0]
dfres["resistance"] = dfres["resistance"].replace({
    'RIFAMPICIN' : 'RIF','ISONIAZID' : 'INH','KANAMYCIN' : 'KAN','PYRAZINAMIDE' : 'PZA','ETHAMBUTOL' : 'EMB',\
    'ETHIONAMIDE' : 'ETH','STREPTOMYCIN' : 'SM','FLUOROQUINOLONE' : 'FQ', 'AMIKACIN' : 'AMI', \
    'CAPREOMYCIN' : 'CAP', 'LINEZOLID' : 'LIN'
})
sorting = ["RIF","INH","PZA","EMB","SM","FQ","KAN","AMI","CAP","ETH","LIN","BDQ","CFZ"]


plot = alt.Chart(dfres).mark_rect(stroke="black",strokeWidth=0.1).encode(
    y=alt.Y("Sample:O",sort=dfres["Sample"].to_list()),
    x=alt.X("resistance:O",axis=alt.Axis(orient="bottom",title="Resistotype",tickWidth=0),sort=sorting),
    color=alt.condition("datum.quality >= 1", alt.ColorValue("#FF3000"), alt.ColorValue("darkorange"))
    
).properties(title="Resistances second and third sample set")
plot

alt.Chart(...)

In [103]:
#Resistance summary set 2 and 3

import pandas as pd
import altair as alt
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)


df = pd.read_csv("/homes/adrian/mdr_mtb-master/results3.run_0-90/coverage.csv", header = 0, sep = '\t')
df['Sample'] = df['Sample'].str.split('_S').str[0]
df = df.loc[df["reduction"] == 0]

df2 = pd.read_csv("/homes/adrian/mdr_mtb-master/resultsSRR_0/coverage.csv", header = 0, sep = '\t')
df2['Sample'] = df2['Sample'].str.replace('SRR22175', '')

dfres = pd.read_csv("/homes/adrian/mdr_mtb-master/results3.run_0-90/resistances.csv", header = 0, sep = '\t')
dfres['Sample'] = dfres['Sample'].str.split('_S').str[0]
dfres["resistance"] = dfres["resistance"].replace({
    'RIFAMPICIN' : 'RIF','ISONIAZID' : 'INH','KANAMYCIN' : 'KAN','PYRAZINAMIDE' : 'PZA','ETHAMBUTOL' : 'EMB',\
    'ETHIONAMIDE' : 'ETH','STREPTOMYCIN' : 'SM','FLUOROQUINOLONE' : 'FQ', 'AMIKACIN' : 'AMI', \
    'CAPREOMYCIN' : 'CAP', 'LINEZOLID' : 'LIN'
})

dfsum = pd.read_csv("/homes/adrian/mdr_mtb-master/results3.run_0-90/summary.csv", header = 0, sep = '\t')
dfsum['Sample'] = dfsum['Sample'].str.split('_S').str[0]
dfsum = dfsum.loc[dfsum["reduction"] == 0]

dfsum2 = pd.read_csv("/homes/adrian/mdr_mtb-master/resultsSRR_0/summary.csv", header = 0, sep = '\t')
dfsum2['Sample'] = dfsum2['Sample'].str.replace('SRR22175', '')

common_cols=list(set.intersection(set(df['Sample']), set(dfres['Sample'])))
df = df[df['Sample'].isin(common_cols)]
dfsum = dfsum[dfsum['Sample'].isin(common_cols)]

dfres2 = pd.read_csv("/homes/adrian/mdr_mtb-master/resultsSRR_0/resistances.csv", header = 0, sep = '\t')
dfres2['Sample'] = dfres2['Sample'].str.split('_S').str[0]
dfres2['Sample'] = dfres2['Sample'].str.replace('SRR22175', '')
dfres2["resistance"] = dfres2["resistance"].replace({
    'RIFAMPICIN' : 'RIF','ISONIAZID' : 'INH','KANAMYCIN' : 'KAN','PYRAZINAMIDE' : 'PZA','ETHAMBUTOL' : 'EMB',\
    'ETHIONAMIDE' : 'ETH','STREPTOMYCIN' : 'SM','FLUOROQUINOLONE' : 'FQ', 'AMIKACIN' : 'AMI', \
    'CAPREOMYCIN' : 'CAP', 'LINEZOLID' : 'LIN'
})
sorting = ["RIF","INH","PZA","EMB","SM","FQ","KAN","AMI","CAP","ETH","LIN","BDQ","CFZ"]

mean3 = alt.Chart(df).mark_bar().encode(
    y=alt.Y("Sample:O"),
    x=alt.X("mean_coverage:Q",scale=alt.Scale(type="linear",align=0),title="Mean locus coverage"),
    color=alt.Color("stabw_coverage",title="Standard deviation",legend=alt.Legend(orient="bottom"))
).properties(width=200)

meanSRR = alt.Chart(df2).mark_bar().encode(
    y=alt.Y("Sample:O",),
    x=alt.X("mean_coverage:Q",scale=alt.Scale(type="linear",align=0),title="Mean locus coverage"),
    color=alt.Color("stabw_coverage",title="Standard deviation",legend=alt.Legend(orient="bottom"))
).properties(width=200)

mut3 = alt.Chart(dfsum).mark_bar(stroke="white",strokeWidth=0.1).encode(
    y=alt.Y("Sample:O",title=None),
    x=alt.X("total_mutation",title="Total mutations"),
    color=alt.Color("res_mutation",title="Resistance mutations",legend=alt.Legend(orient="bottom"))
).properties(width=200)

mutSRR = alt.Chart(dfsum2).mark_bar(stroke="white",strokeWidth=0.1).encode(
    y=alt.Y("Sample:O",title=None),
    x=alt.X("total_mutation",title="Total mutations"),
    color=alt.Color("res_mutation",title="Resistance mutations",legend=alt.Legend(orient="bottom"))
).properties(width=200)

res3 = alt.Chart(dfres).mark_rect(stroke="black",strokeWidth=0.1).encode(
    y=alt.Y("Sample:O",sort=dfres["Sample"].to_list(),axis=alt.Axis(title=None)),
    x=alt.X("resistance:O",axis=alt.Axis(orient="bottom",title="Resistotype",tickWidth=0),sort=sorting),
    color=alt.condition("datum.quality >= 1", alt.ColorValue("#FF3000"), alt.ColorValue("darkorange")))

resSRR = alt.Chart(dfres2).mark_rect(stroke="black",strokeWidth=0.1).encode(
    y=alt.Y("Sample:O",sort=dfres["Sample"].to_list(),axis=alt.Axis(title=None)),
    x=alt.X("resistance:O",axis=alt.Axis(orient="bottom",title="Resistotype",tickWidth=0),sort=sorting),
    color=alt.condition("datum.quality >= 1", alt.ColorValue("#FF3000"), alt.ColorValue("darkorange")))

row1 = alt.hconcat(mean3,res3,mut3,spacing=10,title=alt.TitleParams(text="Second sample set",anchor="middle",fontWeight="bold",fontSize=12)).resolve_scale(color='independent')
row2 = alt.hconcat(meanSRR,resSRR,mutSRR,spacing=10,title=alt.TitleParams(text="Third sample set",anchor="middle",fontWeight="bold",fontSize=12)).resolve_scale(color='independent')
plot = alt.vconcat(row1,row2).resolve_scale(color='independent').properties(
    title=alt.TitleParams(text="Resistance summary",anchor="middle",fontWeight="bold",fontSize=16))
plot

alt.VConcatChart(...)

In [156]:
#Quality Control Boxplot

import pandas as pd
import altair as alt
import altair_catplot as altcat
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)


df = pd.read_csv("/homes/adrian/mdr_mtb-master/results/qubit1.csv", header = 0, sep = ' ')
df2 = pd.read_csv("/homes/adrian/mdr_mtb-master/results/qubit3.csv", header = 0, sep = ' ')
df['Quantity'] = df['Quantity'].str.replace(',', '.')
df['point'] = df['point'].replace({"blp":"before library preparation","alp":"after library preparation"},regex=True)
df2['point'] = df2['point'].replace({"blp":"before library preparation","alp":"after library preparation"},regex=True)
df = df.astype({'Quantity':'float'})

one = altcat.catplot(df,
               height=300,
               width=320,
               mark='point',
               box_mark=dict(opacity=1),
               whisker_mark=dict(strokeWidth=2, opacity=0.9),
               encoding=dict(x=alt.X('point:N',sort=['before library preparation','after library preparation'],title='1.Set',axis=alt.Axis(orient="bottom",labelAngle=0,labelFontSize=10,tickWidth=0,domain=False)),
                             y=alt.Y('Quantity:Q',title='Quantity [ng/µl]',scale=alt.Scale(domain=(0, 55)) ),
                             color=alt.Color('point:N', legend=None)),
              transform="box").properties(width=200)

two = altcat.catplot(df2,
               height=300,
               width=320,
               mark='point',
               box_mark=dict(opacity=1),
               whisker_mark=dict(strokeWidth=2, opacity=0.9),
               encoding=dict(x=alt.X('point:N',sort=['before library preparation','after library preparation'],title='2.Set',axis=alt.Axis(orient="bottom",labelAngle=0,labelFontSize=10,tickWidth=0,domain=False)),
                             y=alt.Y('Quantity:Q',title=None,axis=alt.Axis(labels=False,ticks=False,domain=False)),
                             color=alt.Color('point:N', legend=None)),
              transform="box")

plot = alt.hconcat(one,two).properties(spacing=-5,
    title=alt.TitleParams(text="Quality control results",anchor="middle",fontWeight="bold",fontSize=16))
plot


alt.HConcatChart(...)